<a href="https://colab.research.google.com/github/xharles2994/Tensorflow_models/blob/main/Title_Object_detection_on_football_highlight_dataset_CV.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

1.	Introduction

 •	Brief overview of EfficientDet

 •	Problem statement on Video dataset

2.	Data preparation

 •	Data pre-processing (e.g. resizing, normalization)

 •	Splitting data into training, validation, and test sets

3.	Model setup

 •	Choosing EfficientDet model variant

 •	Setting up the model architecture

 •	Preparing input pipelines (e.g. using TFRecords)

4.	Training

 •	Training process (e.g. optimization algorithm, learning rate schedule)

 •	Monitoring training progress (e.g. using TensorBoard)

 •	Saving checkpoints and evaluating model performance

5.	Inference

 •	Running inference on the whole video

 •	Post-processing (e.g. non-maximum suppression)

 •	Visualizing results (e.g. drawing bounding boxes on frames)
6.	Conclusion

 •	Summary of project and results achieved ( Combined frames into a single 30s Video


##1. EfficientDet Model
EfficientDet is an efficient and accurate object detection model that builds on the architecture of EfficientNet. It uses a compound scaling method to optimize the depth, width, and resolution of the network, as well as other design choices such as a bi-directional feature pyramid network and a weighted feature fusion strategy to further improve efficiency. EfficientDet has achieved top scores on several benchmarks for object detection, including COCO and PASCAL VOC, and is highly scalable to different sizes and types of objects and computational budgets.

###Problem Statement on Video Dataset

The problem statement is as follows:

Football coaches face a significant challenge in analyzing game footage to make informed tactical and formation decisions. With limited time and resources, coaches are forced to rely on their subjective interpretations of game footage, which may not always be accurate. To address this challenge, this project aims to develop an object detection model that can accurately identify and localize players from each team in a 60-second football highlight video of a match between Chelsea and Manchester United. The proposed model will use bounding boxes to identify the location of each player in the frame and label them according to their respective team. By accurately identifying players from each team, coaches can gain valuable insights into player positioning and movement, which can help them make informed decisions about tactics and formations. Overall, this project aims to provide coaches with an objective and accurate analysis of game footage, which can help improve their team's performance on the pitch.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


##2. Data Preparation
 Here the first process is to breakdown the video into frames/s. Once we have all our frames we can label the images (bounding box ) using ROBOFLOW https://app.roboflow.com/.

In [ ]:
import cv2
import os

video_path = "/content/drive/MyDrive/ML Portfolio/deepsort_30sec (2).mp4"
output_folder = "/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/Image_dataset"

# Create output folder if it doesn't exist
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

cap = cv2.VideoCapture(video_path)
count = 0

while(cap.isOpened()):
    ret, frame = cap.read()

    if ret == False:
        break

    # Define output file path with numeric name
    output_path = os.path.join(output_folder, f"{count}.jpg")

    # Write frame to output file
    cv2.imwrite(output_path, frame)

    count += 1

cap.release()
cv2.destroyAllWindows()


Code to download labeled dataset from Roboflow, the dataset is downloaded in TF.record format, this enables easy processing by the model.

In [ ]:
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="B8QXQaigq9lZkz5H77w6")
project = rf.workspace("charles2994-spdui").project("soccer-xtoid")
dataset = project.version(3).download("tfrecord")

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.8/55.8 kB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.8/67.8 kB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.5/54.5 kB 7.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.8/58.8 kB 9.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for wget: filename=wget-3.2-py3-none-any.whl size=9676 sha256=345cc9177230d63fead0b61912a4543cd4741442df4fc938726b13acc510f963
  Stored in directory: /root/.cache/pip/wheels/04/5f/3e/46cc37c5d698415694d83f607f833f83f0149e49b3af9d0f38
Successfully built wget
  Attempting uninstall: pyparsing
    Found existing installation: pyparsing 3.0.9
    Uninstalling pyparsing-3.0.9:
      Successfully uninstalled pyparsing-3.0.9
  Attempting uninstall: idna
    Found existing installation: idna 3.4
    Uninstalling idna-3.4:
    

loading Roboflow workspace...
loading Roboflow project...


Extracting Dataset Version Zip to SOCCER-3 in tfrecord:: 100%|██████████| 11/11 [00:00<00:00, 1215.04it/s]


In [ ]:
# NOTE: Update these TFRecord names from "cells" and "cells_label_map" to your files!
test_record_fname = '/content/SOCCER-3/test/PLAYERS-.tfrecord'
train_record_fname = '/content/SOCCER-3/train/PLAYERS-.tfrecord'
label_map_pbtxt_fname = '/content/SOCCER-3/train/PLAYERS-_label_map.pbtxt'

##3.Setting up the model architecture

EfficientDet is a state-of-the-art object detection model introduced by Google researchers in 2019.
EfficientDet builds on the popular object detection framework, RetinaNet, but makes several key improvements. The model uses a compound scaling method to scale up the depth, width, and resolution of the network, resulting in better accuracy and faster inference times. Additionally, EfficientDet introduces a novel scaling technique called "BiFPN" (bidirectional feature pyramid network), which enhances the feature representation across different scales of the image.

The architecture of EfficientDet consists of a backbone network, a feature pyramid network (FPN), and the BiFPN module. The backbone network is a convolutional neural network that extracts features from the input image. The FPN network generates a multi-scale feature pyramid from the backbone features, which is used to detect objects of different sizes in the image. Finally, the BiFPN module aggregates information across different scales of the feature pyramid, allowing the model to make more accurate predictions.

EfficientDet has achieved state-of-the-art performance on several object detection benchmarks, including COCO and Pascal VOC, while being much more computationally efficient than previous state-of-the-art models. This makes it a promising architecture for a variety of real-world object detection applications, particularly those with limited computational resources.


Install dependencies and Clone TENSORFLOW github repository

In [ ]:
!pip install tensorflow==2.9.0
!apt install --allow-change-held-packages libcudnn8=8.7.0.77-1+cuda11.2

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 511.7/511.7 MB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.6/42.6 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.8/5.8 MB 96.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 82.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 438.7/438.7 kB 45.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.9/4.9 MB 110.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 70.3 MB/s eta 0:00:00
  Attempting uninstall: keras
    Found existing installation: keras 2.12.0
    Uninstalling keras-2.12.0:
      Successfully uninstalled keras-2.12.0
  Attempting uninstall: flatbuffers
    Found existing installation: flatbuffers 23.3.3
    Uninstalling flatbuffers-23.3.3:
      Successfully uninstalled flatbuffers-23.3.3
  Attempting uni

Reading package lists... Done
Building dependency tree       
Reading state information... Done
E: Version '8.7.0.77-1+cuda11.2' for 'libcudnn8' was not found


Clone the EfficientDet model from the Github repo

In [ ]:
#Install github repo for EfficientDet Model
import os
import pathlib

# Clone the tensorflow models repository if it doesn't already exist
if "models" in pathlib.Path.cwd().parts:
  while "models" in pathlib.Path.cwd().parts:
    os.chdir('..')
elif not pathlib.Path('models').exists():
  !git clone --depth 1 https://github.com/tensorflow/models

Cloning into 'models'...
remote: Enumerating objects: 3706, done.
remote: Counting objects: 100% (3706/3706), done.
remote: Compressing objects: 100% (2817/2817), done.
remote: Total 3706 (delta 1052), reused 1815 (delta 840), pack-reused 0
Receiving objects: 100% (3706/3706), 48.71 MiB | 16.67 MiB/s, done.
Resolving deltas: 100% (1052/1052), done.


From cloned repository install tensorflow object APIs

In [ ]:
!pip uninstall numpy

Found existing installation: numpy 1.22.4
Uninstalling numpy-1.22.4:
  Would remove:
    /usr/local/bin/f2py
    /usr/local/bin/f2py3
    /usr/local/bin/f2py3.9
    /usr/local/lib/python3.9/dist-packages/numpy-1.22.4.dist-info/*
    /usr/local/lib/python3.9/dist-packages/numpy.libs/libgfortran-040039e1.so.5.0.0
    /usr/local/lib/python3.9/dist-packages/numpy.libs/libopenblas64_p-r0-2f7c42d4.3.18.so
    /usr/local/lib/python3.9/dist-packages/numpy.libs/libquadmath-96973f99.so.0.0.0
    /usr/local/lib/python3.9/dist-packages/numpy/*
Proceed (Y/n)? y
  Successfully uninstalled numpy-1.22.4


In [ ]:
# Install the Object Detection API
%%bash
cd models/research
protoc object_detection/protos/*.proto --python_out=.
cp object_detection/packages/tf2/setup.py .
python -m pip install .

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Processing /content/models/research
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.5/14.5 MB 66.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 66.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 28.0/28.0 MB 45.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.6/116.6 kB 16.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 84.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 630.1/630.1 kB 59.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.0/6.0 MB 77.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━

In [ ]:
!pip install numpy==1.19.3

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.9/14.9 MB 54.0 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 1.23.5
    Uninstalling numpy-1.23.5:
      Successfully uninstalled numpy-1.23.5
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
xarray 2022.12.0 requires numpy>=1.20, but you have numpy 1.19.3 which is incompatible.
xarray-einstats 0.5.1 requires numpy>=1.20, but you have numpy 1.19.3 which is incompatible.
tf-models-official 2.12.0 requires numpy>=1.20, but you have numpy 1.19.3 which is incompatible.
tensorflow 2.12.0 requires numpy<1.24,>=1.22, but you have numpy 1.19.3 which is incompatible.
tensorflow-model-optimization 0.7.4 requires numpy~=1.23, but you have numpy 1.19.3 which is incompatible.
scipy 1.10.1 r

Import Packages

In [ ]:
import matplotlib
import matplotlib.pyplot as plt

import os
import random
import io
import imageio
import glob
import scipy.misc
import numpy as np
from six import BytesIO
from PIL import Image, ImageDraw, ImageFont
from IPython.display import display, Javascript
from IPython.display import Image as IPyImage

import tensorflow as tf

from object_detection.utils import label_map_util
from object_detection.utils import config_util
from object_detection.utils import visualization_utils as viz_utils
from object_detection.utils import colab_utils
from object_detection.builders import model_builder


%matplotlib inline



TensorFlow Addons (TFA) has ended development and introduction of new features.
TFA has entered a minimal maintenance and release mode until a planned end of life in May 2024.
Please modify downstream libraries to take dependencies from other repositories in our TensorFlow community (e.g. Keras, Keras-CV, and Keras-NLP). 

For more information see: https://github.com/tensorflow/addons/issues/2807 



In [ ]:
!pip uninstall tensorflow numpy

Found existing installation: tensorflow 2.12.0
Uninstalling tensorflow-2.12.0:
  Would remove:
    /usr/local/bin/estimator_ckpt_converter
    /usr/local/bin/import_pb_to_tensorboard
    /usr/local/bin/saved_model_cli
    /usr/local/bin/tensorboard
    /usr/local/bin/tf_upgrade_v2
    /usr/local/bin/tflite_convert
    /usr/local/bin/toco
    /usr/local/bin/toco_from_protos
    /usr/local/lib/python3.9/dist-packages/tensorflow-2.12.0.dist-info/*
    /usr/local/lib/python3.9/dist-packages/tensorflow/*
Proceed (Y/n)? y
  Successfully uninstalled tensorflow-2.12.0
Found existing installation: numpy 1.19.3
Uninstalling numpy-1.19.3:
  Would remove:
    /usr/local/bin/f2py
    /usr/local/bin/f2py3
    /usr/local/bin/f2py3.9
    /usr/local/lib/python3.9/dist-packages/numpy-1.19.3.dist-info/*
    /usr/local/lib/python3.9/dist-packages/numpy.libs/libgfortran-2e0d59d6.so.5.0.0
    /usr/local/lib/python3.9/dist-packages/numpy.libs/libopenblasp-r0-a32f1dca.3.12.so
    /usr/local/lib/python3.9/dist

In [ ]:
!pip install tensorflow numpy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached tensorflow-2.12.0-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (585.9 MB)
  Using cached numpy-1.24.2-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.3 MB)
  Using cached numpy-1.23.5-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.1 MB)


In [ ]:
#run model builder test
!python /content/models/research/object_detection/builders/model_builder_tf2_test.py

2023-04-13 13:45:15.314104: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
/usr/local/lib/python3.9/dist-packages/tensorflow_addons/utils/tfa_eol_msg.py:23: UserWarning: 

TensorFlow Addons (TFA) has ended development and introduction of new features.
TFA has entered a minimal maintenance and release mode until a planned end of life in May 2024.
Please modify downstream libraries to take dependencies from other repositories in our TensorFlow community (e.g. Keras, Keras-CV, and Keras-NLP). 

For more information see: https://github.com/tensorflow/addons/issues/2807 

  warnings.warn(
Running tests under Python 3.9.16: /usr/bin/python3
[ RUN      ] ModelBuilderTF2Test.test_create_center_net_deepmac
2023-04-13 13:45:23.343326: W tensorflow/core/common_runtime/gpu/gpu_bfc_allocator.cc:47] Overriding orig_value setting because the TF_FORCE_GPU_ALLOW_GROWTH environment variable is set. Original config value was 0.
W0413 13:45:23.407356 139767

This code helps visualize the prediction and box bounding

In [ ]:
def load_image_into_numpy_array(path):
  """Load an image from file into a numpy array.

  Puts image into numpy array to feed into tensorflow graph.
  Note that by convention we put it into a numpy array with shape
  (height, width, channels), where channels=3 for RGB.

  Args:
    path: a file path.

  Returns:
    uint8 numpy array with shape (img_height, img_width, 3)
  """
  img_data = tf.io.gfile.GFile(path, 'rb').read()
  image = Image.open(BytesIO(img_data))
  (im_width, im_height) = image.size
  return np.array(image.getdata()).reshape(
      (im_height, im_width, 3)).astype(np.uint8)

def plot_detections(image_np,
                    boxes,
                    classes,
                    scores,
                    category_index,
                    figsize=(12, 16),
                    image_name=None):
  """Wrapper function to visualize detections.

  Args:
    image_np: uint8 numpy array with shape (img_height, img_width, 3)
    boxes: a numpy array of shape [N, 4]
    classes: a numpy array of shape [N]. Note that class indices are 1-based,
      and match the keys in the label map.
    scores: a numpy array of shape [N] or None.  If scores=None, then
      this function assumes that the boxes to be plotted are groundtruth
      boxes and plot all boxes as black with no classes or scores.
    category_index: a dict containing category dictionaries (each holding
      category index `id` and category name `name`) keyed by category indices.
    figsize: size for the figure.
    image_name: a name for the image file.
  """
  image_np_with_annotations = image_np.copy()
  viz_utils.visualize_boxes_and_labels_on_image_array(
      image_np_with_annotations,
      boxes,
      classes,
      scores,
      category_index,
      use_normalized_coordinates=True,
      min_score_thresh=0.8)
  if image_name:
    plt.imsave(image_name, image_np_with_annotations)
  else:
    plt.imshow(image_np_with_annotations)

Configure the EfficientDet for customization


In [ ]:
##change chosen model to deploy different models available in the TF2 object detection zoo
MODELS_CONFIG = {
    'efficientdet-d0': {
        'model_name': 'efficientdet_d0_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d0_512x512_coco17_tpu-8.config',
        'pretrained_checkpoint': 'efficientdet_d0_coco17_tpu-32.tar.gz',
        'batch_size': 4
    },
    'efficientdet-d1': {
        'model_name': 'efficientdet_d1_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d1_640x640_coco17_tpu-8.config',
        'pretrained_checkpoint': 'efficientdet_d1_coco17_tpu-32.tar.gz',
        'batch_size': 4
    },
    'efficientdet-d2': {
        'model_name': 'efficientdet_d2_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d2_768x768_coco17_tpu-8.config',
        'pretrained_checkpoint': 'efficientdet_d2_coco17_tpu-32.tar.gz',
        'batch_size': 4
    },
        'efficientdet-d3': {
        'model_name': 'efficientdet_d3_coco17_tpu-32',
        'base_pipeline_file': 'ssd_efficientdet_d3_896x896_coco17_tpu-32.config',
        'pretrained_checkpoint': 'efficientdet_d3_coco17_tpu-32.tar.gz',
        'batch_size': 4
    }
}

#in this tutorial we implement the lightweight, smallest state of the art efficientdet model
#if you want to scale up tot larger efficientdet models you will likely need more compute!
chosen_model = 'efficientdet-d0'

num_steps = 4000 #The more steps, the longer the training. Increase if your loss function is still decreasing and validation metrics are increasing.
num_eval_steps = 500 #Perform evaluation after so many steps

model_name = MODELS_CONFIG[chosen_model]['model_name']
pretrained_checkpoint = MODELS_CONFIG[chosen_model]['pretrained_checkpoint']
base_pipeline_file = MODELS_CONFIG[chosen_model]['base_pipeline_file']
batch_size = MODELS_CONFIG[chosen_model]['batch_size'] #if you can fit a large batch in memory, it may speed up your training

In [ ]:
#download pretrained weights
%mkdir "/content/models/research/deploy/"
%cd "/content/models/research/deploy/"
import tarfile
download_tar = 'http://download.tensorflow.org/models/object_detection/tf2/20200711/' + pretrained_checkpoint

!wget {download_tar}
tar = tarfile.open(pretrained_checkpoint)
tar.extractall()
tar.close()

/content/models/research/deploy
--2023-04-13 13:46:13--  http://download.tensorflow.org/models/object_detection/tf2/20200711/efficientdet_d0_coco17_tpu-32.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 142.251.12.128, 2404:6800:4003:c11::80
Connecting to download.tensorflow.org (download.tensorflow.org)|142.251.12.128|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 30736482 (29M) [application/x-tar]
Saving to: ‘efficientdet_d0_coco17_tpu-32.tar.gz’

efficientdet_d0_coc 100%[===================>]  29.31M  48.3MB/s    in 0.6s    

2023-04-13 13:46:14 (48.3 MB/s) - ‘efficientdet_d0_coco17_tpu-32.tar.gz’ saved [30736482/30736482]



In [ ]:
#download base training configuration file
%cd /content/models/research/deploy
download_config = 'https://raw.githubusercontent.com/tensorflow/models/master/research/object_detection/configs/tf2/' + base_pipeline_file
!wget {download_config}

/content/models/research/deploy
--2023-04-13 13:49:11--  https://raw.githubusercontent.com/tensorflow/models/master/research/object_detection/configs/tf2/ssd_efficientdet_d0_512x512_coco17_tpu-8.config
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.108.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4630 (4.5K) [text/plain]
Saving to: ‘ssd_efficientdet_d0_512x512_coco17_tpu-8.config’

ssd_efficientdet_d0 100%[===================>]   4.52K  --.-KB/s    in 0s      

2023-04-13 13:49:12 (25.5 MB/s) - ‘ssd_efficientdet_d0_512x512_coco17_tpu-8.config’ saved [4630/4630]



In [ ]:
#prepare
pipeline_fname = '/content/models/research/deploy/' + base_pipeline_file
fine_tune_checkpoint = '/content/models/research/deploy/' + model_name + '/checkpoint/ckpt-0'

def get_num_classes(pbtxt_fname):
    from object_detection.utils import label_map_util
    label_map = label_map_util.load_labelmap(pbtxt_fname)
    categories = label_map_util.convert_label_map_to_categories(
        label_map, max_num_classes=90, use_display_name=True)
    category_index = label_map_util.create_category_index(categories)
    return len(category_index.keys())
num_classes = get_num_classes(label_map_pbtxt_fname)

In [ ]:
num_classes

3

In [ ]:
#write custom configuration file by slotting our dataset, model checkpoint, and training parameters into the base pipeline file

import re

%cd "/content/models/research/deploy"
print('writing custom configuration file')

with open(pipeline_fname) as f:
    s = f.read()
with open('pipeline_file.config', 'w') as f:

    # fine_tune_checkpoint
    s = re.sub('fine_tune_checkpoint: ".*?"',
               'fine_tune_checkpoint: "{}"'.format(fine_tune_checkpoint), s)

    # tfrecord files train and test.
    s = re.sub(
        '(input_path: ".*?)(PATH_TO_BE_CONFIGURED/train)(.*?")', 'input_path: "{}"'.format(train_record_fname), s)
    s = re.sub(
        '(input_path: ".*?)(PATH_TO_BE_CONFIGURED/val)(.*?")', 'input_path: "{}"'.format(test_record_fname), s)

    # label_map_path
    s = re.sub(
        'label_map_path: ".*?"', 'label_map_path: "{}"'.format(label_map_pbtxt_fname), s)

    # Set training batch_size.
    s = re.sub('batch_size: [0-9]+',
               'batch_size: {}'.format(batch_size), s)

    # Set training steps, num_steps
    s = re.sub('num_steps: [0-9]+',
               'num_steps: {}'.format(num_steps), s)

    # Set number of classes num_classes.
    s = re.sub('num_classes: [0-9]+',
               'num_classes: {}'.format(num_classes), s)

    #fine-tune checkpoint type
    s = re.sub(
        'fine_tune_checkpoint_type: "classification"', 'fine_tune_checkpoint_type: "{}"'.format('detection'), s)

    f.write(s)

/content/models/research/deploy
writing custom configuration file


In [ ]:
#This line of code is a sanity check for the model
%cat /content/models/research/deploy/pipeline_file.config


 # SSD with EfficientNet-b0 + BiFPN feature extractor,
# shared box predictor and focal loss (a.k.a EfficientDet-d0).
# See EfficientDet, Tan et al, https://arxiv.org/abs/1911.09070
# See Lin et al, https://arxiv.org/abs/1708.02002
# Trained on COCO, initialized from an EfficientNet-b0 checkpoint.
#
# Train on TPU-8

model {
  ssd {
    inplace_batchnorm_update: true
    freeze_batchnorm: false
    num_classes: 3
    add_background_class: false
    box_coder {
      faster_rcnn_box_coder {
        y_scale: 10.0
        x_scale: 10.0
        height_scale: 5.0
        width_scale: 5.0
      }
    }
    matcher {
      argmax_matcher {
        matched_threshold: 0.5
        unmatched_threshold: 0.5
        ignore_thresholds: false
        negatives_lower_than_unmatched: true
        force_match_for_each_row: true
        use_matmul_gather: true
      }
    }
    similarity_calculator {
      iou_similarity {
      }
    }
    encode_background_as_zeros: true
    anchor_generator {
      m

pipeline_file: location of custom training configuration declared below /n

model_dir: the location that the tensorboard logs and saved model checkpoints will save to declared below

In [ ]:
pipeline_file = '/content/models/research/deploy/pipeline_file.config'
model_dir = '/content/SOCCER-3/train'

num_train_steps:  /n

num_eval_steps: /n

RUN TRAINING

##4. Training
See the python code to drive data through the pipeline and commence training, the model weights are saved in the model_dir. num_train_steps identifies how many training iterartions.

In [ ]:
!python /content/models/research/object_detection/model_main_tf2.py \
    --pipeline_config_path={pipeline_file} \
    --model_dir={model_dir} \
    --alsologtostderr \
    --num_train_steps={num_steps} \
    --sample_1_of_n_eval_examples=1 \
    --num_eval_steps={num_eval_steps}

2023-04-13 13:50:17.408559: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
/usr/local/lib/python3.9/dist-packages/tensorflow_addons/utils/tfa_eol_msg.py:23: UserWarning: 

TensorFlow Addons (TFA) has ended development and introduction of new features.
TFA has entered a minimal maintenance and release mode until a planned end of life in May 2024.
Please modify downstream libraries to take dependencies from other repositories in our TensorFlow community (e.g. Keras, Keras-CV, and Keras-NLP). 

For more information see: https://github.com/tensorflow/addons/issues/2807 

  warnings.warn(
2023-04-13 13:50:22.571271: W tensorflow/core/common_runtime/gpu/gpu_bfc_allocator.cc:47] Overriding orig_value setting because the TF_FORCE_GPU_ALLOW_GROWTH environment variable is set. Original config value was 0.
INFO:tensorflow:Using MirroredStrategy with devices ('/job:localhost/replica:0/task:0/device:GPU:0',)
I0413 13:50:22.602257 139942543939392 mirr

Should show loss grapghs for inspection

In [ ]:
%reload_ext tensorboard
%tensorboard --logdir '/content/SOCCER-3/train/'

ERROR: Failed to launch TensorBoard (exited with 1).
Contents of stderr:
2023-04-13 14:18:56.233384: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
/usr/local/lib/python3.9/dist-packages/tensorboard_data_server/bin/server: /lib/x86_64-linux-gnu/libc.so.6: version `GLIBC_2.33' not found (required by /usr/local/lib/python3.9/dist-packages/tensorboard_data_server/bin/server)
/usr/local/lib/python3.9/dist-packages/tensorboard_data_server/bin/server: /lib/x86_64-linux-gnu/libc.so.6: version `GLIBC_2.34' not found (required by /usr/local/lib/python3.9/dist-packages/tensorboard_data_server/bin/server)
/usr/local/lib/python3.9/dist-packages/tensorboard_data_server/bin/server: /lib/x86_64-linux-gnu/libc.so.6: version `GLIBC_2.32' not found (required by /usr/local/lib/python3.9/dist-packages/tensorboard_data_server/bin/server)
Address already in use
Port 6006 is in use by another program. Either identify and stop that program, or start the server 

CODESECTIONS BELOW HELP CHOOSE A CHECKPOINT AND EXPORT TO A .PY file

In [ ]:
#see where the model saved weights
%ls '/content/drive/MyDrive/Efficientdet/SOCCER-2/train'

checkpoint                  ckpt-3.index
ckpt-1.data-00000-of-00001  ckpt-4.data-00000-of-00001
ckpt-1.index                ckpt-4.index
ckpt-2.data-00000-of-00001  PLAYERS-_label_map.pbtxt
ckpt-2.index                PLAYERS-.tfrecord
ckpt-3.data-00000-of-00001  train/


Save model and checkpoints to a directory

In [ ]:
#run conversion script
import re
import numpy as np

output_directory = '/content/SOCCER-3/test'

#place the model weights you would like to export here
last_model_path = '/content/SOCCER-3/train'
print(last_model_path)
!python //content/models/research/object_detection/exporter_main_v2.py \
    --trained_checkpoint_dir {last_model_path} \
    --output_directory {output_directory} \
    --pipeline_config_path {pipeline_file}

/content/SOCCER-3/train
2023-04-13 14:26:09.442431: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
/usr/local/lib/python3.9/dist-packages/tensorflow_addons/utils/tfa_eol_msg.py:23: UserWarning: 

TensorFlow Addons (TFA) has ended development and introduction of new features.
TFA has entered a minimal maintenance and release mode until a planned end of life in May 2024.
Please modify downstream libraries to take dependencies from other repositories in our TensorFlow community (e.g. Keras, Keras-CV, and Keras-NLP). 

For more information see: https://github.com/tensorflow/addons/issues/2807 

  warnings.warn(
2023-04-13 14:26:12.789443: W tensorflow/core/common_runtime/gpu/gpu_bfc_allocator.cc:47] Overriding orig_value setting because the TF_FORCE_GPU_ALLOW_GROWTH environment variable is set. Original config value was 0.
I0413 14:26:12.812833 139860733146944 ssd_efficientnet_bifpn_feature_extractor.py:150] EfficientDet EfficientNet backbon

In [ ]:
%ls '/content/SOCCER-3/test/saved_model'

assets/  fingerprint.pb  saved_model.pb  variables/


##5. Inference

Running Inference on the whole dataset not just the testset.
Reason is cause we want to remerge the image frames to become a 60s video again with a inclusion of bounding Box.

In [ ]:
import matplotlib
import matplotlib.pyplot as plt

import io
import scipy.misc
import numpy as np
from six import BytesIO
from PIL import Image, ImageDraw, ImageFont

import tensorflow as tf

from object_detection.utils import label_map_util
from object_detection.utils import config_util
from object_detection.utils import visualization_utils as viz_utils
from object_detection.builders import model_builder

%matplotlib inline

In [ ]:
def load_image_into_numpy_array(path):
  """Load an image from file into a numpy array.

  Puts image into numpy array to feed into tensorflow graph.
  Note that by convention we put it into a numpy array with shape
  (height, width, channels), where channels=3 for RGB.

  Args:
    path: the file path to the image

  Returns:
    uint8 numpy array with shape (img_height, img_width, 3)
  """
  img_data = tf.io.gfile.GFile(path, 'rb').read()
  image = Image.open(BytesIO(img_data))
  (im_width, im_height) = image.size
  return np.array(image.getdata()).reshape(
      (im_height, im_width, 3)).astype(np.uint8)

LISTS OF CHECK POINTS TO CHOOSE FROM

In [ ]:
%ls '/content/SOCCER-3/train'

checkpoint                  ckpt-4.data-00000-of-00001
ckpt-1.data-00000-of-00001  ckpt-4.index
ckpt-1.index                ckpt-5.data-00000-of-00001
ckpt-2.data-00000-of-00001  ckpt-5.index
ckpt-2.index                PLAYERS-_label_map.pbtxt
ckpt-3.data-00000-of-00001  PLAYERS-.tfrecord
ckpt-3.index                train/


REBUILD AND ACCESS OBJECT DETECTION MODEL

In [ ]:
#recover our saved model
pipeline_config = pipeline_file
#generally you want to put the last ckpt from training in here
model_dir = '/content/SOCCER-3/train'
configs = config_util.get_configs_from_pipeline_file(pipeline_config)
model_config = configs['model']
detection_model = model_builder.build(
      model_config=model_config, is_training=False)

# Restore checkpoint
ckpt = tf.compat.v2.train.Checkpoint(
      model=detection_model)
ckpt.restore(os.path.join('/content/SOCCER-3/train/ckpt-4'))


def get_model_detection_function(model):
  """Get a tf.function for detection."""

  @tf.function
  def detect_fn(image):
    """Detect objects in image."""

    image, shapes = model.preprocess(image)
    prediction_dict = model.predict(image, shapes)
    detections = model.postprocess(prediction_dict, shapes)

    return detections, prediction_dict, tf.reshape(shapes, [-1])

  return detect_fn

detect_fn = get_model_detection_function(detection_model)

In [ ]:
#map labels for test data decoding
label_map_path = configs['eval_input_config'].label_map_path
label_map = label_map_util.load_labelmap(label_map_path)
categories = label_map_util.convert_label_map_to_categories(
    label_map,
    max_num_classes=label_map_util.get_max_label_map_index(label_map),
    use_display_name=True)
category_index = label_map_util.create_category_index(categories)
label_map_dict = label_map_util.get_label_map_dict(label_map, use_display_name=True)

RUN OBJECT DETECTOR ON YOUR ALL IMAGE



In [ ]:
import glob
import os
import random
import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf
from object_detection.utils import visualization_utils as viz_utils

# Directory paths
TEST_IMAGE_FOLDER = '/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/Image_dataset'
OUTPUT_FOLDER = '/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images'

# Load the model
detect_fn = detect_fn # Load your object detection model here
category_index = category_index # Define your category index mapping here

# Get all image file paths in the test image folder
TEST_IMAGE_PATHS = glob.glob(os.path.join(TEST_IMAGE_FOLDER, '*.jpg'))

# Loop through all the images
for image_path in TEST_IMAGE_PATHS:

    # Load image
    image_np = load_image_into_numpy_array(image_path)

    input_tensor = tf.convert_to_tensor(
        np.expand_dims(image_np, 0), dtype=tf.float32)
    detections, predictions_dict, shapes = detect_fn(input_tensor)

    label_id_offset = 1
    image_np_with_detections = image_np.copy()

    viz_utils.visualize_boxes_and_labels_on_image_array(
        image_np_with_detections,
        detections['detection_boxes'][0].numpy(),
        (detections['detection_classes'][0].numpy() + label_id_offset).astype(int),
        detections['detection_scores'][0].numpy(),
        category_index,
        use_normalized_coordinates=True,
        max_boxes_to_draw=200,
        min_score_thresh=.5,
        agnostic_mode=False,
    )

    # Save image with bounding boxes
    output_image_path = os.path.join(OUTPUT_FOLDER, os.path.basename(image_path))
    plt.imsave(output_image_path, image_np_with_detections)

    print(f'Saved image with bounding boxes: {output_image_path}')

print('Done!')


Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/0.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/1.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/2.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/3.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/4.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/5.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/6.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/7.jpg
Saved image with bounding boxes: /content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images/8.jpg
Saved image with bo

Merge all images to become a 60s video

In [ ]:
#Move Efficiendet to destination folder
import shutil

source_directory = "/content/models"
destination_directory = "/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet"

# Move the directory
shutil.move(source_directory, destination_directory)

'/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/models'

In [ ]:
#Move dataset to destination folder
import shutil

source_directory = "/content/SOCCER-3"
destination_directory = "/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet"

# Move the directory
shutil.move(source_directory, destination_directory)

'/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/SOCCER-3'

In [ ]:
import cv2
import os

# Define the input folder containing the image frames
input_folder = '/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detected_images'

# Define the output video file path and filename
output_video = '/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detetction_video.mp4'

# Define the frame rate of the output video
frame_rate = 25

# Get the list of image filenames in the input folder
image_filenames = os.listdir(input_folder)

# Sort the image filenames by their numerical index
image_filenames.sort(key=lambda x: int(x.split('.')[0]))

# Set the width and height of the video frames
frame_width = 640
frame_height = 480

# Create a video writer object
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter(output_video, fourcc, frame_rate, (frame_width, frame_height))

# Iterate through the image filenames and add each frame to the video
for image_filename in image_filenames:
    # Read the image frame from file
    frame = cv2.imread(os.path.join(input_folder, image_filename))

    # Resize the frame to the desired width and height
    frame = cv2.resize(frame, (frame_width, frame_height))

    # Add the frame to the video
    out.write(frame)

# Release the video writer object and close the output file
out.release()


In [ ]:
from IPython.display import HTML
from base64 import b64encode
import os

# Input video path
save_path = "/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/detetction_video.mp4"

# Compressed video path
compressed_path = "/content/drive/MyDrive/PORTFOLIO/Dataset/Efficientdet/result_compressed.mp4"

os.system(f"ffmpeg -i {save_path} -vcodec libx264 {compressed_path}")

# Show video
mp4 = open(compressed_path,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=640 loop=10 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)
